In [2]:
import pandas as pd
import numpy as np
import networkx as nx
import plotly.express as px
import plotly.graph_objects as go
from sktime.distances import dtw_distance, pairwise_distance

ImportError: cannot import name 'dtw_distance' from 'sktime.distances' (unknown location)

In [6]:
# import data
rets = pd.read_csv('crypto_data_500.csv', parse_dates = ['timestamp'], index_col = 'timestamp')

In [7]:
# filter those that have more than 10% missing values
mask = rets.isnull().sum() <= 152
rets = rets.loc[:, mask]

# forward fill with most recent values and drop the rest
rets = rets.ffill().dropna()

# double check there are no missing values
rets.isnull().sum().sum()

0

In [8]:
# calc daily log returns
log_rets = np.log(rets).diff().dropna()

In [9]:
# correlation matrix
log_rets.corr()

bitcoin_price  ethereum_price  tether_price  \
bitcoin_price                1.000000        0.834744     -0.157480   
ethereum_price               0.834744        1.000000     -0.144859   
tether_price                -0.157480       -0.144859      1.000000   
binance-coin_price           0.698230        0.734514     -0.079094   
usd-coin_price              -0.220664       -0.200155      0.886542   
...                               ...             ...           ...   
v-id_price                   0.434154        0.466318     -0.000422   
aeternity_price              0.530148        0.551547     -0.052558   
streamr-datacoin_price       0.523959        0.537807     -0.056640   
pivx_price                   0.556124        0.557054     -0.071842   
neblio_price                 0.465838        0.464682     -0.026651   

                        binance-coin_price  usd-coin_price  ripple_price  \
bitcoin_price                     0.698230       -0.220664      0.595695   
ethereum_price                    0.734514       -0.200155      0.645205   
tether_price                     -0.079094        0.886542     -0.099318   
binance-coin_price                1.000000       -0.136348      0.583344   
usd-coin_price                   -0.136348        1.000000     -0.127964   
...                                    ...             ...           ...   
v-id_price                        0.431082       -0.037260      0.344268   
aeternity_price                   0.534716       -0.121949      0.522388   
streamr-datacoin_price            0.518299       -0.082185      0.463735   
pivx_price                        0.535290       -0.106063      0.496498   
neblio_price                      0.459076       -0.057646      0.395886   

                        okb_price  cardano_price  dogecoin_price  \
bitcoin_price            0.538971       0.685228        0.441461   
ethereum_price           0.540278       0.748439        0.436925   
tether_price            -0.031965      -0.112956       -0.040530   
binance-coin_price       0.670280       0.653396        0.343287   
usd-coin_price          -0.065846      -0.169362       -0.084691   
...                           ...            ...             ...   
v-id_price               0.321638       0.400931        0.178386   
aeternity_price          0.385617       0.520952        0.327268   
streamr-datacoin_price   0.402564       0.502374        0.262894   
pivx_price               0.435096       0.531394        0.312843   
neblio_price             0.336617       0.411814        0.226715   

                        matic-network_price  ...  bitcoin-diamond_price  \
bitcoin_price                      0.564105  ...               0.503560   
ethereum_price                     0.637980  ...               0.489405   
tether_price                      -0.041728  ...              -0.085249   
binance-coin_price                 0.623748  ...               0.421576   
usd-coin_price                    -0.068290  ...              -0.103475   
...                                     ...  ...                    ...   
v-id_price                         0.350855  ...               0.266474   
aeternity_price                    0.456630  ...               0.390817   
streamr-datacoin_price             0.480350  ...               0.337905   
pivx_price                         0.465766  ...               0.374202   
neblio_price                       0.389545  ...               0.295998   

                        monacoin_price  bitshares_price  tpt_price  \
bitcoin_price                 0.510994         0.592159   0.374965   
ethereum_price                0.511081         0.598198   0.368204   
tether_price                 -0.079852        -0.076164  -0.058504   
binance-coin_price            0.476380         0.542529   0.330309   
usd-coin_price               -0.133714        -0.121675  -0.082004   
...                                ...              ...        ...   
v-id_price                    0.251267         0.2

In [10]:
# as heatmap
px.imshow(log_rets.corr())

In [7]:
# calculate the dtw_matrix for MST
N = log_rets.shape[1]
dtw_matrix = np.zeros((N, N))

for i in range(N):
    if i % 20 == 0:
        print(f"On round: {i}")
    for j in range(N):
        dtw_matrix[i, j] = dtw_distance(log_rets.values[:, i], log_rets.values[:, j])

On round: 0
On round: 20
On round: 40
On round: 60
On round: 80
On round: 100
On round: 120
On round: 140
On round: 160
On round: 180


In [11]:
with open('dtw_unstandardized.npy', 'wb') as f:
    np.save(f, dtw_matrix)

In [11]:
log_means = log_rets.mean(axis = 0)
log_stds  = log_rets.std(axis = 0)

log_rets -= log_means
log_rets /= log_stds

In [18]:
# calculate the dtw_matrix for MST
N           = log_rets.shape[1]
dtw_matrix2 = np.zeros((N, N))

for i in range(N):
    if i % 20 == 0:
        print(f"On round: {i}")
    for j in range(N):
        dtw_matrix2[i, j] = dtw_distance(log_rets.values[:, i], log_rets.values[:, j])
        
print(f"Exporting to saved notebook")
with open('dtw_standardized.npy', 'wb') as f:
    np.save(f, dtw_matrix2)

On round: 0
On round: 20
On round: 40
On round: 60
On round: 80
On round: 100
On round: 120
On round: 140
On round: 160
On round: 180
Exporting to saved notebook


In [18]:
px.imshow(dtw_matrix2)